In [1]:
!pip install -U transformers
!pip install -U accelerate #git+https://github.com/huggingface/accelerate.git
!pip install -U bitsandbytes #git+ https://github.com/timdettmers/bitsandbytes.git

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 26.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 30.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 83.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 70.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.2/244.2 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.6/92.6 MB 8.2 MB/s eta 0:00:00


In [2]:
from transformers import AutoTokenizer, AutoModelForCausalLM

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("cerebras/btlm-3b-8k-base")
model = AutoModelForCausalLM.from_pretrained(
    "cerebras/btlm-3b-8k-base",
    trust_remote_code=True,
    torch_dtype="auto",
    load_in_8bit=True,
    offload_folder="offload",
  )

# Set the prompt for generating text
prompt = "Albert Einstein was known for "

# Tokenize the prompt and convert to PyTorch tensors
inputs = tokenizer(prompt, return_tensors="pt")

# Generate text using the model
outputs = model.generate(
    **inputs,
    num_beams=5,
    max_new_tokens=50,
    early_stopping=True,
    no_repeat_ngram_size=2
)

# Convert the generated token IDs back to text
generated_text = tokenizer.batch_decode(outputs, skip_special_tokens=True)

# Print the generated text
print(generated_text[0])

A new version of the following files was downloaded from https://huggingface.co/cerebras/btlm-3b-8k-base:
- configuration_btlm.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


A new version of the following files was downloaded from https://huggingface.co/cerebras/btlm-3b-8k-base:
- modeling_btlm.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1468: UserWarning: You are calling .generate() with the `input_ids` being on a device type different than your model's device. `input_ids` is on cpu, whereas the model is on cuda. You may experience unexpected behaviors or slower generation. Please make sure that you have put `input_ids` to the correct device by calling for example input_ids = input_ids.to('cuda') before running `.generate()`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/bitsandbytes/autograd/_functions.py:322: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


Albert Einstein was known for 
his theory of relativity and his work on the photoelectric effect.
He was awarded the 1921 Nobel Prize in Physics "for his services
to theoretical physics, and especially for his discovery of the law
which unifies in a single equation the


In [3]:
print(model)

BTLMLMHeadModel(
  (transformer): BTLMModel(
    (wte): Embedding(50257, 2560)
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0-31): 32 x BTLMBlock(
        (ln_1): LayerNorm((2560,), eps=1e-05, elementwise_affine=True)
        (attn): BTLMAttention(
          (c_attn): Linear8bitLt(in_features=2560, out_features=7680, bias=True)
          (c_proj): Linear8bitLt(in_features=2560, out_features=2560, bias=True)
          (attn_dropout): Dropout(p=0.0, inplace=False)
          (resid_dropout): Dropout(p=0.0, inplace=False)
        )
        (ln_2): LayerNorm((2560,), eps=1e-05, elementwise_affine=True)
        (mlp): BTLMMLP(
          (c_fc): Linear8bitLt(in_features=2560, out_features=6826, bias=True)
          (c_fc2): Linear8bitLt(in_features=2560, out_features=6826, bias=True)
          (c_proj): Linear8bitLt(in_features=6826, out_features=2560, bias=True)
          (act): SwiGLUActivation()
          (dropout): Dropout(p=0.0, inplace=False)
        )
      )
 

In [4]:
list_vars = model.state_dict()
for name in list_vars.keys():
    print(name, "=>", list_vars[name])


transformer.wte.weight => tensor([[ 0.0200,  0.0442,  0.0562,  ...,  0.0173, -0.0238, -0.0889],
        [-0.0259,  0.0170, -0.0221,  ..., -0.0752, -0.0635,  0.0947],
        [-0.0276,  0.1846,  0.1533,  ..., -0.0195,  0.0299,  0.0796],
        ...,
        [ 0.1182,  0.1523,  0.0742,  ..., -0.1162,  0.0177,  0.0991],
        [ 0.0220, -0.0579,  0.0125,  ..., -0.0576,  0.0327,  0.0211],
        [ 0.0508, -0.0217,  0.0278,  ..., -0.0308, -0.0378,  0.0013]],
       device='cuda:0', dtype=torch.bfloat16)
transformer.h.0.ln_1.weight => tensor([0.6445, 0.7344, 0.6133,  ..., 0.6484, 0.7070, 0.7148], device='cuda:0',
       dtype=torch.bfloat16)
transformer.h.0.ln_1.bias => tensor([ 0.0288,  0.0082, -0.0771,  ...,  0.0284, -0.0391,  0.0233],
       device='cuda:0', dtype=torch.bfloat16)
transformer.h.0.attn.c_attn.weight => tensor([[ 15,   3, -15,  ...,  67,  40,  29],
        [ -4,  43,  26,  ...,   9,  15,  19],
        [ 41,  33,   6,  ..., -20, -27, -35],
        ...,
        [ 27, -51,   

In [5]:
import sys
import os
import struct
import json

import torch
from transformers import AutoConfig

config = AutoConfig.from_pretrained("cerebras/btlm-3b-8k-base", trust_remote_code=True)
hparams = config.to_dict()
fname_out = "btlm-3b.ggml.bin"

print(json.dumps(hparams, indent=4, sort_keys=True))



{
    "_name_or_path": "cerebras/btlm-3b-8k-base",
    "activation_function": "swiglu",
    "add_cross_attention": false,
    "architectures": [
        "BTLMLMHeadModel"
    ],
    "attn_pdrop": 0.0,
    "auto_map": {
        "AutoConfig": "cerebras/btlm-3b-8k-base--configuration_btlm.BTLMConfig",
        "AutoModel": "cerebras/btlm-3b-8k-base--modeling_btlm.BTLMModel",
        "AutoModelForCausalLM": "cerebras/btlm-3b-8k-base--modeling_btlm.BTLMLMHeadModel",
        "AutoModelForQuestionAnswering": "cerebras/btlm-3b-8k-base--modeling_btlm.BTLMForQuestionAnswering",
        "AutoModelForSequenceClassification": "cerebras/btlm-3b-8k-base--modeling_btlm.BTLMForSequenceClassification",
        "AutoModelForTokenClassification": "cerebras/btlm-3b-8k-base--modeling_btlm.BTLMForTokenClassification"
    },
    "bad_words_ids": null,
    "begin_suppress_tokens": null,
    "bos_token_id": 50256,
    "chunk_size_feed_forward": 0,
    "cross_attention_hidden_size": null,
    "decoder_start_token

In [6]:
import re
import numpy as np

fout = open(fname_out, "wb")

fout.write(struct.pack("i", 0x67676D6C))
fout.write(struct.pack("i", hparams["vocab_size"]))
fout.write(struct.pack("i", hparams["n_positions"]))
fout.write(struct.pack("i", hparams["n_embd"]))
fout.write(struct.pack("i", hparams["n_head"]))
fout.write(struct.pack("i", hparams["n_layer"]))
fout.write(struct.pack("i", hparams["n_inner"]))
fout.write(struct.pack("i", 1))

for i in range(hparams["vocab_size"]):
  text = tokenizer.decode([i]).encode('utf-8')
  fout.write(struct.pack("i", len(text)))
  fout.write(text)


# for name in list_vars.keys():
#     print(name, "=>", list_vars[name])


for name in list_vars.keys():
    if name[-14:] == ".weight_format":
      print("FOUND " + name)
      continue




    print("Processing variable: " + name)
    data = list_vars[name].squeeze().cpu().type(dtype=torch.float16).numpy()
    print(" with shape: ", data.shape)

    # rename headers to keep compatibility
    if name == "transformer.ln_f.weight":
        name = "model/ln_f/g"
    elif name == "transformer.ln_f.bias":
        name = "model/ln_f/b"
    elif name == "transformer.wte.weight":
        name = "model/wte"
    elif name == "transformer.wpe.weight":
        name = "model/wpe"
    elif name == "lm_head.weight":
        name = "model/lm_head"
    elif name == "transformer.relative_pe.slopes":
      name = "model/relative_pe/slopes"
    elif re.match(r"transformer.h\.\d+\.ln_1\.weight", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/ln_1/g"
    elif re.match(r"transformer.h\.\d+\.ln_1\.bias", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/ln_1/b"
    elif re.match(r"transformer.h\.\d+\.attn\.c_attn\.weight", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/attn/c_attn/w"
    elif re.match(r"transformer.h\.\d+\.attn\.c_attn\.bias", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/attn/c_attn/b"
    elif re.match(r"transformer.h\.\d+\.attn\.c_proj\.weight", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/attn/c_proj/w"
    elif re.match(r"transformer.h.\d+.attn.c_proj.bias", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/attn/c_proj/b"
    elif re.match(r"transformer.h.\d+.ln_2.weight", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/ln_2/g"
    elif re.match(r"transformer.h.\d+.ln_2.bias", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/ln_2/b"
    elif re.match(r"transformer.h.\d+.mlp.c_fc.weight", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_fc/w"
    elif re.match(r"transformer.h.\d+.mlp.c_fc.bias", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_fc/b"
    elif re.match(r"transformer.h.\d+.mlp.c_proj.weight", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_proj/w"
    elif re.match(r"transformer.h.\d+.mlp.c_proj.bias", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_proj/b"
    # NEW
    elif re.match(r"transformer.h.\d+.attn.c_proj.SCB", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/attn/c_proj/scb"
    elif re.match(r"transformer.h.\d+.attn.c_attn.SCB", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/attn/c_attn/scb"
    elif re.match(r"transformer.h.\d+.mlp.c_fc.SCB", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_fc/scb"
    elif re.match(r"transformer.h.\d+.mlp.c_fc2.weight", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_fc2/w"
    elif re.match(r"transformer.h.\d+.mlp.c_fc2.bias", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_fc2/b"
    elif re.match(r"transformer.h.\d+.mlp.c_fc2.SCB", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_fc2/scb"
    elif re.match(r"transformer.h.\d+.mlp.c_proj.SCB", name):
        i = re.findall("\d+", name)[0]
        name = f"model/h{i}/mlp/c_proj/scb"

    else:
        print("Unrecognized variable name. %s", name)


    n_dims = len(data.shape);

    # ftype == 0 -> float32, ftype == 1 -> float16
    ftype = 1;
    print("  Converting to float16")
    data = data.astype(np.float16)
    ftype = 8


    # for efficiency - transpose the projection matrices
    # "model/h.*/attn/c_attn/w"
    # "model/h.*/attn/c_proj/w"
    # "model/h.*/mlp/c_fc/w"
    # "model/h.*/mlp/c_proj/w"
    if name[-14:] == "/attn/c_attn/w" or \
       name[-14:] == "/attn/c_proj/w" or \
       name[-11:] == "/mlp/c_fc/w" or \
       name[-13:] == "/mlp/c_proj/w":
        print("  Transposing")
        data = data.transpose()

    # header
    str = name.encode('utf-8')
    fout.write(struct.pack("iii", n_dims, len(str), ftype))
    for i in range(n_dims):
        fout.write(struct.pack("i", data.shape[n_dims - 1 - i]))
    fout.write(str);

    # data
    data.tofile(fout)

fout.close()

print("Done. Output file: " + fname_out)
print("")


# write_binary()






Processing variable: transformer.wte.weight
 with shape:  (50257, 2560)
  Converting to float16
Processing variable: transformer.h.0.ln_1.weight
 with shape:  (2560,)
  Converting to float16
Processing variable: transformer.h.0.ln_1.bias
 with shape:  (2560,)
  Converting to float16
Processing variable: transformer.h.0.attn.c_attn.weight
 with shape:  (7680, 2560)
  Converting to float16
  Transposing
Processing variable: transformer.h.0.attn.c_attn.bias
 with shape:  (7680,)
  Converting to float16
Processing variable: transformer.h.0.attn.c_attn.SCB
 with shape:  (7680,)
  Converting to float16
FOUND transformer.h.0.attn.c_attn.weight_format
Processing variable: transformer.h.0.attn.c_proj.weight
 with shape:  (2560, 2560)
  Converting to float16
  Transposing
Processing variable: transformer.h.0.attn.c_proj.bias
 with shape:  (2560,)
  Converting to float16
Processing variable: transformer.h.0.attn.c_proj.SCB
 with shape:  (2560,)
  Converting to float16
FOUND transformer.h.0.attn.c

In [9]:
from huggingface_hub import login, HfApi

login()

api = HfApi()

api.upload_file(
    path_or_fileobj="/content/btlm-3b.ggml.bin",
    path_in_repo="btlm-3b.ggml.bin",
    repo_id="bornjre/btlm-3b-ggml",
    repo_type="model",
)

# api.upload_folder(
#     folder_path="/content/btlm-3b-ggml",
#     repo_id="bornjre/btlm-3b-ggml",
#     repo_type="model",
# )

btlm-3b.ggml.bin:   0%|          | 0.00/5.56G [00:00<?, ?B/s]

'https://huggingface.co/bornjre/btlm-3b-ggml/blob/main/btlm-3b.ggml.bin'